# Funções

## Coordenadas

In [1]:
def coordenadas(ax_size = (-2,2), plane = True, opacity = 0.7):
    u, v = var('y, z')
    size = (ax_size[1] - ax_size[0])
    u_ = (u, ax_size[0], ax_size[1]) # dimensão dos eixos / planos
    v_ = (v, ax_size[0], ax_size[1]) # dimensão dos eixos / planos

    x = parametric_plot((u, 0, 0), u_,  opacity=1, color='red')
    x += vector([ax_size[1],0,0]).plot(color = 'red')
    labels = text3d('x',1.1*vector([ax_size[1],0,0]),fontsize= str(50*size)+'%')
    
    y = parametric_plot((0, u, 0), u_,  opacity=1, color='yellow')
    y += vector([0,ax_size[1],0]).plot(color = 'yellow')
    labels += text3d('y',1.1*vector([0,ax_size[1],0]),fontsize= str(50*size)+'%')
    
    z = parametric_plot((0, 0, u), u_,  opacity=1) # Blue
    z += vector([0,0,ax_size[1]]).plot(color = 'blue')
    labels += text3d('z',1.1*vector([0,0,ax_size[1]]),fontsize= str(50*size)+'%')
    
    if plane == True:
        
        cont = ax_size[0]
        xy = parametric_plot((u, cont, 0), u_, opacity=opacity, color='black')
        xy += parametric_plot((cont, u, 0), u_, opacity=opacity, color='black')
        while cont != ax_size[1]:

            cont += size/10
            xy += parametric_plot((u, cont, 0), u_, opacity=opacity, color='black')
            xy += parametric_plot((cont, u, 0), u_, opacity=opacity, color='black')
        return xy + x + y + z + labels # planos

    return x + y + z + labels #eixos
    

## Translação

In [55]:
def translacao(objeto, vector):
    num_linhas = 0
    for i in objeto:
        num_linhas +=1
    objeto = objeto + matrix([list(vector)]*num_linhas)
    return objeto

## Rotação em torno do eixo x

In [70]:
def matriz_rotx(α):
    matriz = matrix([[1, 0, 0], [0, cos(α), -sin(α)], [0, sin(α), cos(α)]])
    return matriz

## Rotação em torno do eixo y

In [71]:
def matriz_roty(α):
    matriz = matrix([[cos(α), 0, sin(α)], [0, 1, 0], [-sin(α), 0, cos(α)]])
    return matriz

## Rotação em torno do eixo z

In [3]:
def matriz_rotz(α):
    matriz = matrix([[cos(α), -sin(α), 0], [sin(α), cos(α), 0], [0, 0, 1]])
    return matriz

## Rotação em torno de um eixo qualquer

In [87]:
def matriz_rot(θ, vetor_direcao): # O vetor deve ser unitario, caso contrario apresentara erros
    x = vetor_direcao[0]
    y = vetor_direcao[1]
    z = vetor_direcao[2]
    
    if x == 0 and y == 0 and z == 0:
        print("Insira uma direção válida!")
        return None
        
    #Calculando angulos de rotação 
    α = arcsin(y / sqrt(x**2 + y**2).n()).n() # Angulo da projeção do vetor no plano xy
    β = arcsin( z / sqrt(x**2 + y**2 + z**2).n() ).n() # Angulo da projeção do vetor no plano xz
   
    # Calculando eixo auxliar para uma rotação vertical
    if x == 0 and y == 0:
        α = 0
        
    matriz_rot_horizontal = matrix([[cos(α), -sin(α), 0], [sin(α), cos(α), 0], [0, 0, 1]]) # matriz transformação ao redor do eixo z (rotação horizontal)
    matriz_rot_vertical = matriz_roty(-β)

    matriz_rot_eixo_arb = matriz_rotx(θ)

    matriz_rot_horizontal_ret = matrix([[cos(-α), -sin(-α), 0], [sin(-α), cos(-α), 0], [0, 0, 1]]) # matriz transformação ao redor do eixo z (rotação horizontal)
    matriz_rot_vertical_ret = matriz_roty(β)


    matriz_rot = matriz_rot_horizontal * matriz_rot_vertical * matriz_rot_eixo_arb * matriz_rot_vertical_ret * matriz_rot_horizontal_ret
    
    return matriz_rot

Polyhedron(cubo * matriz_rot(pi.n(), vector([1,1,1]))).plot() + coordenadas(ax_size=(-5,5))

Graphics3d Object

## Rotação em torno do propio eixo

In [117]:
def matriz_roteixo(objeto, θ, vetor_direcao, centro_massa):
    objeto = translacao(objeto, (-1)*centro_massa)
    objeto = objeto * matriz_rot(θ, vetor_direcao)
    objeto = translacao(objeto, centro_massa)
    return objeto

cubo = matrix(polytopes.cube().vertices()) + matrix([[3,3,1]]*8)
frames = [Polyhedron(matriz_roteixo(cubo, k, vector([0,0,1]), centro_massa = vector([3,3,1])), base_ring = QQ).plot() for k in (0, 0.1, ..,pi.n())]
plot = animate(frames).interactive()
plot + coordenadas(ax_size = (-5,5))

Graphics3d Object

## Mudança de escala

In [5]:
def matriz_escala(γ):
    matriz = matrix([[1/γ,0,0],[0,1,0],[0,0,1]])
    return matriz

## transformação de Lorentz

In [67]:
def matriz_translor(vetor_direcao, γ):
    # Coordenadas do vetor_direção, vetor ao qual há movimento e portanto contração
    x = vetor_direcao[0]
    y = vetor_direcao[1]
    z = vetor_direcao[2]
    #Calculando angulos de rotação 
    α = arcsin(y / sqrt(x**2 + y**2).n()).n() # Angulo da projeção do vetor no plano xy
    β = arcsin( z / sqrt(x**2 + y**2 + z**2).n() ).n() # Angulo da projeção do vetor no plano xz
   
    # Calculando eixo auxliar para uma rotação vertical
    if x == 0 and y == 0:
        α = 0
        

    # Multiplicando rotação horizontal e vertical
    matriz_rot_horizontal = matrix([[cos(α), -sin(α), 0], [sin(α), cos(α), 0], [0, 0, 1]]) # matriz transformação ao redor do eixo z (rotação horizontal)
    matriz_rot_vertical = matriz_roty(-β)
    
    matriz_transf = matriz_rot_horizontal * matriz_rot_vertical # aplicamos a rotação vertical
    
    # Aplicando a contração de lorentz
    matriz_transf = matriz_transf * matrix([[1/γ,0,0],[0,1,0],[0,0,1]])
    
    # Retornamos o objeto a sua posição inicial
    matriz_rot_vertical_retorno = matriz_roty(β)
    matriz_rot_horizontal_retorno = matrix([[cos(-α), -sin(-α), 0], [sin(-α), cos(-α), 0], [0, 0, 1]])
    
    matriz_transf = matriz_transf * matriz_rot_vertical_retorno * matriz_rot_horizontal_retorno
    
    
    return matriz_transf

cubo = matrix(polytopes.cube().vertices()) + matrix([[1,1,1]]*8)
tetra = matrix(polytopes.tetrahedron().vertices())
Polyhedron(tetra).plot() + coordenadas()
Polyhedron(cubo * matriz_translor(vector([0,0,1]), 2)).plot() + coordenadas(ax_size = (-5,5))

Graphics3d Object

# Variáveis e objetos

## Variáveis

In [7]:
# DEFINIR VARIAVEIS

# variáveis simbólicas
y, z = var('y, z') 
α, β = var('α, β') 
γ = var('γ')

# 'Constante'
c = 1 # velocidade da luz
l = 2 # lado do do objeto
o = 0 # origem do objeto

# Relações

#Calculando angulos de rotação
vetor_direcao = vector([x,y,z])
α = arcsin( y / sqrt(x**2 + y**2))
β = arcsin( z / sqrt(x**2 + y**2 + z**2) )
vetor_auxiliar = vetor_direcao * matrix([[cos(α), -sin(α), 0], [sin(α), cos(α), 0], [0, 0, 1]]) #
vetor_auxiliar = vector([vetor_auxiliar[0], vetor_auxiliar[1], 0]) # projeção do vetor_auxiliar no plano xy
vetor_auxiliar = vetor_auxiliar * matrix([[cos(-pi.n()/2), -sin(-pi.n()/2), 0], [sin(-pi.n()/2), cos(-pi.n()/2), 0], [0, 0, 1]]) # vetor ortogonal ao vetor_auxiliar


## Objetos

In [60]:
quadrado = [[0,o,o,0], [0,o,o+l,0], [0,o+l,o+l,0], [0,o+l,o,0], [0,o,o,0]]
cubo = matrix(polytopes.cube().vertices())

# Construção da matriz dado uma direção genérica

# Animação

## Utilizando a função matriz_translor()

In [63]:
cubo = matrix(polytopes.cube().vertices()) + matrix([[1,1,1]]*8)
frames = [Polyhedron(cubo * matriz_translor(vector([1,0,0]), k), base_ring=QQ).plot() for k in (1, 1.1,..5)]
plot = animate(frames).interactive()

In [22]:
plot + coordenadas(ax_size=(-5,5))

Graphics3d Object

In [23]:
cubo2 = matrix(polytopes.cube().vertices()) + matrix([[1,1,1]]*8)
frames2 = [Polyhedron(cubo * matriz_translor(vector([0,0,1]), k), base_ring=QQ).plot() for k in (1, 1.1,..5)]
plot2 = animate(frames2).interactive()

NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN
NaN


In [24]:
plot2 + coordenadas(ax_size=(-5,5))

Graphics3d Object

In [25]:
cubo3 = matrix(polytopes.cube().vertices()) + matrix([[1,1,1]]*8)
frames3 = [Polyhedron(cubo * matriz_translor(vector([1,1,1]), k), base_ring=QQ).plot() for k in (1, 1.1,..5)]
plot3 = animate(frames3).interactive()

0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448
0.785398163397448


In [26]:
plot3 + coordenadas(ax_size=(-5,5))

Graphics3d Object

In [36]:
cubo4 = matrix(polytopes.cube().vertices()) + matrix([[1,1,1]]*8)
frames4 = [Polyhedron(cubo * matriz_translor(vector([1,1,1]), k), base_ring=QQ).plot() for k in (1, 1.01,..5)]
plot4 = animate(frames4).interactive()

In [37]:
plot4 + coordenadas(ax_size=(-5,5))

Graphics3d Object

In [127]:
vel_ang1 = 0
vel_ang2 = 0
gamma = 1
cubot = cubo
frames = []
cubo = matrix(polytopes.cube().vertices()) + matrix([[3,3,1]]*8)

for f in range(0,20):
    frames += [Polyhedron(matriz_roteixo(cubo, θ = vel_ang1, vetor_direcao = vector([0,0,1]), centro_massa = vector([3,3,1])) * matriz_translor(vector([0,0,1]), gamma)).plot()]
    #frames += [Polyhedron(matriz_roteixo(cubo, θ = vel_ang1, vetor_direcao = vector([0,1,0]), centro_massa = vector([3,3,1]))).plot()]
    vel_ang1 += pi.n()/20
    gamma += 1/20 
plot = animate(frames).interactive()
plot + coordenadas(ax_size = (-5,5))

Graphics3d Object

In [ ]:
vetor_teste = vector([1,1,1])

vetor_teste = vetor_teste * matriz_rotz(pi.n()/4)
vetor_teste = vetor_teste * matriz_roty(-arcsin(1/sqrt(3).n()).n())

vetor_teste.plot() + coordenadas()

In [51]:
asd = [[1,1,1]]
matrix(asd*10)

[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]
[1 1 1]